In [86]:
import numpy as np
import folium
from folium.plugins import HeatMapWithTime,HeatMap

# latitude and longitude in Singapore city
coordinate_sentosa = [1.248946, 103.834306]
coordinate_orchard_road = [1.304247, 103.833264]
coordinate_changi_airport = [1.357557, 103.98847]
coordinate_nus = [1.296202,103.776899]
coordinate_ntu = [1.34841, 103.682933]
coordinate_zoo = [1.403717, 103.793974]
coordinate_ang_mo_kio = [1.37008, 103.849523]
coordinate_yi_shun = [1.429384, 103.835028]

# icon 
icon_cloud = "cloud"
icon_sign = "info-sign"
# # define the city map
# city_map = folium.Map(location=coordinate_orchard_road, zoom_start=11)

# # 使用 numpy 建立初始数据
# initial_data = (np.random.normal(size=(200, 2)) *
#                 np.array([[0.02, 0.02]]) +
#                 np.array([coordinate_orchard_road]))

# # 建立连续的数据
# data = [initial_data.tolist()]
# for i in range(20):
#     data.append((data[i] + np.random.normal(size=(200, 2)) * 0.001).tolist())

# # 显示连续的热力图
# city_map.add_child(HeatMapWithTime(data)) 
# city_map

In [87]:
import pickle
with open("/home/Gong.gz/Public_Dataset/ncbdc2021/time_range_avg_heat_map/avg_list_24_hour_filled.pkl" , 'rb') as f:
    average_energy_list = pickle.load(f)
    
print(len(average_energy_list))


24


In [88]:
i_range,j_range = list(average_energy_list[0].keys())[-1]
list(average_energy_list[0].keys())[-1]

(21, 12)

In [89]:
import math


def millerToXY(lon, lat):
    """
    经纬度转换为平面坐标系中的x,y 利用米勒坐标系
    :param lon: 经度
    :param lat: 维度
    :return:
    """
    xy_coordinate = []  # 转换后的XY坐标集
    L = 6381372 * math.pi * 2
    W = L
    H = L / 2
    mill = 2.3
    x = lon * math.pi / 180
    y = lat * math.pi / 180
    y = 1.25 * math.log(math.tan(0.25 * math.pi + 0.4 * y))
    x = (W / 2) + (W / (2 * math.pi)) * x
    y = (H / 2) - (H / (2 * mill)) * y
    xy_coordinate.append((int(round(x)), int(round(y))))
    return xy_coordinate


def millerToLonLat(x, y):
    """
    将平面坐标系中的x,y转换为经纬度，利用米勒坐标系
    :param x: x轴
    :param y: y轴
    :return:
    """
    lonlat_coordinate = []
    L = 6381372 * math.pi * 2
    W = L
    H = L / 2
    mill = 2.3
    lat = ((H / 2 - y) * 2 * mill) / (1.25 * H)
    lat = ((math.atan(math.exp(lat)) - 0.25 * math.pi) * 180) / (0.4 * math.pi)
    lon = (x - W / 2) * 360 / W
    # TODO 最终需要确认经纬度保留小数点后几位
    lonlat_coordinate.append((round(lon, 7), round(lat, 7)))
    return lonlat_coordinate


def tfGrid2FoliumHeatmapData(base_x,
                             base_y,
                             grid,
                             is_mul_normal=False,
                             interval=1000):
    """
    @description  : 将网格数据（字典类型）转化为含经纬度的数据，格式List((Lat,Lon,weight(Normalized to 0-1)))
    ---------
    @param  :
    -------
    @Returns  :
    -------
    """
    data = []
    min_energy = 0
    max_energy = 10000
    x_range, y_range = list(grid.keys())[-1]
    for xx in range(x_range + 1):
        for yy in range(y_range + 1):
            energy = grid[(xx, yy)]
            if (energy > max_energy):
                energy = max_energy
            elif (energy <= min_energy):
                energy = min_energy + 100 
                # energy = min_energy
            energy = (energy - min_energy) / (max_energy - min_energy)

            if not is_mul_normal:
                mean = ((2 * xx + 1) * interval / 2,
                        (2 * yy + 1) * interval / 2)
                lon, lat = millerToLonLat(mean[0] + base_x,
                                          mean[1] + base_y)[0]
                data.append([lat, lon, energy])
            else:
                cov = [[(800 / 8)**2, 0], [0, (800 / 8)**2]]
                for iii in range(10):
                    noise = np.random.multivariate_normal([0, 0], cov)
                    energy_noise = np.random.rand()
                    mean = ((2 * xx + 1) * interval / 2,
                            (2 * yy + 1) * interval / 2)
                    lon, lat = millerToLonLat(mean[0] + base_x + noise[0],
                                              mean[1] + base_y + noise[1])[0]

                    data.append([lat, lon, energy])
    return data


In [90]:
min_x = 33003950.0
min_y = 6815930.0
origin = millerToLonLat(min_x,min_y)
data_test = tfGrid2FoliumHeatmapData(min_x,min_y,average_energy_list[0])
data_test[0][2]

0.01

In [91]:
folium_data = []
for i in range(len(average_energy_list)):
    folium_data.append(tfGrid2FoliumHeatmapData(min_x,min_y,average_energy_list[i],is_mul_normal=True))
    
folium_data

[[[39.9221641, 116.3335645, 0.01],
  [39.9212408, 116.3346843, 0.01],
  [39.9229689, 116.3347354, 0.01],
  [39.9244909, 116.3330194, 0.01],
  [39.9229958, 116.3352094, 0.01],
  [39.92287, 116.3334182, 0.01],
  [39.9244155, 116.3350529, 0.01],
  [39.9233623, 116.3342166, 0.01],
  [39.9227891, 116.3331563, 0.01],
  [39.9235117, 116.3329587, 0.01],
  [39.9131153, 116.3328698, 0.01],
  [39.9107355, 116.3351922, 0.01],
  [39.9113799, 116.3329487, 0.01],
  [39.9098583, 116.3345945, 0.01],
  [39.910965, 116.3334278, 0.01],
  [39.9098076, 116.3335196, 0.01],
  [39.9113753, 116.3341976, 0.01],
  [39.9101429, 116.3331027, 0.01],
  [39.912044, 116.3336117, 0.01],
  [39.9116593, 116.3329523, 0.01],
  [39.90033, 116.3344562, 0.01],
  [39.8999022, 116.333256, 0.01],
  [39.9027756, 116.3330486, 0.01],
  [39.8990024, 116.3332464, 0.01],
  [39.9031328, 116.3341123, 0.01],
  [39.8989334, 116.3348881, 0.01],
  [39.8997304, 116.3349844, 0.01],
  [39.9013765, 116.332979, 0.01],
  [39.8999067, 116.3337621, 

In [92]:
mark_latitude = 39.9164
mark_longitude = 116.5086

city_map = folium.Map(
    location=[origin[0][1], origin[0][0]],
    zoom_start=11,
    # tiles=
    # 'http://webrd02.is.autonavi.com/appmaptile?lang=zh_cn&size=1&scale=1&style=7&x={x}&y={y}&z={z}',
    control_scale=True,  # 比例尺
    attr='default')
# city_map.add_child(HeatMap(folium_data[0]))
city_map.add_child(HeatMapWithTime(folium_data))

# plot rectangle
x_range, y_range = list(average_energy_list[0].keys())[-1]
for xx in range(x_range + 1):
    for yy in range(y_range + 1):
        # 矩形
        bounds = [
            [millerToLonLat(min_x+1000*xx, min_y+1000*(yy+1))[0][1],
             millerToLonLat(min_x+1000*xx, min_y+1000*(yy+1))[0][0]],
            [millerToLonLat(min_x+1000*(xx+1), min_y+1000*yy)[0][1],
             millerToLonLat(min_x+1000*(xx+1), min_y+1000*yy)[0][0]]]

        city_map.add_child(folium.Rectangle(
            # 坐标列表, Latitude and Longitude of line (Northing, Easting)
            bounds=bounds,
            weight=2,  # 线条宽度
            color='dodgerblue'))

city_map.add_child(folium.LatLngPopup())

city_map


In [93]:
average_energy_list

[{(0, 0): 0.0,
  (0, 1): 0.0,
  (0, 2): 0.0,
  (0, 3): 9137.974375118201,
  (0, 4): 6339.06787481551,
  (0, 5): 0.0,
  (0, 6): 0.0,
  (0, 7): 5491.465500000002,
  (0, 8): 0.0,
  (0, 9): 0.0,
  (0, 10): 370.43999999999994,
  (0, 11): 0.0,
  (0, 12): 0.0,
  (1, 0): 0.0,
  (1, 1): 0.0,
  (1, 2): 0.0,
  (1, 3): 0.0,
  (1, 4): 6049.410750000002,
  (1, 5): 0.0,
  (1, 6): 0.0,
  (1, 7): 2458.958343758947,
  (1, 8): 4308.485859406349,
  (1, 9): 4780.095803611178,
  (1, 10): 0.0,
  (1, 11): 0.0,
  (1, 12): 0.0,
  (2, 0): 0.0,
  (2, 1): 0.0,
  (2, 2): 0.0,
  (2, 3): 0.0,
  (2, 4): 0.0,
  (2, 5): 2892.94545001684,
  (2, 6): 0.0,
  (2, 7): 6128.978867626075,
  (2, 8): 36889.748999999996,
  (2, 9): 1139.2072499557928,
  (2, 10): 0.0,
  (2, 11): 0.0,
  (2, 12): 0.0,
  (3, 0): 0.0,
  (3, 1): 0.0,
  (3, 2): 0.0,
  (3, 3): 0.0,
  (3, 4): 0.0,
  (3, 5): 3774.1002715744503,
  (3, 6): 5062.757999936853,
  (3, 7): 0.7548529238882171,
  (3, 8): 9957.474300000003,
  (3, 9): 651.3959999999998,
  (3, 10): 3378